# Exercise 4: **Fourier Analysis, PCA and Clustering**


### Basics of Biomedical Data Analysis

**Stephane Deny**: stephane.deny@aalto.fi

**Carlos Sevilla Salcedo**: carlos.sevillasalcedo@aalto.fi

**Hyunkyung Choo**: hyunkyung.choo@aalto.fi

<br></br>
<center><img src="https://drive.google.com/uc?export=view&id=1pKi7IMOOe_huyEyBTj4mfAEF6EJ_kdp2" width="40%">
</center>



In this exercise, we will analyse a biological temporal signal using Fourier analysis, Principal Component Analysis (PCA), and the K-means clustering method.

# 1. Dataset and problem description

The retina sends the visual information to the brain via electric signals, sent through the optic nerve (*Figure 1*). The retinal code is the language with which the retina communicates with the brain. It has been extensively studied by neuroscientists.

In this problem, a rat retina has been placed on a grid of electrode and is being stimulated with a movie. The signals emitted by ganglion cells, the output neurons of the retina, are recorded by the electrodes. The dataset consists of a recording from **one electrode** during **one minute** of movie stimulation. The sampling frequency of the recording is 20,000 Hz.

The ganglion cells emit 'spikes', short electrical impulses conveyed through the optic nerve. Each ganglion cell produces spikes with a unique waveform: you can think of it as an electrical fingerprint which is unique to the cell. One problem we face is that one electrode might record spikes from more than one cell in its surroundings, which makes it difficult to study the cells' responses in isolation.

In this exercise, we will use a high-pass filter to pre-process the temporal trace recorded by the electrode. Next, we will apply principal component analysis and a clustering method to isolate the spikes originating from different cells.


<br></br>
<center>
    <img src="https://drive.google.com/uc?export=view&id=10T-KTyEZE6BbZMHrEUefD5PYvlxReDpg" width="90%">
<em>

Figure 1.</em> <strong>A.</strong> The retina is a neural tissue which covers the interior wall of the eye. The eye lens projects an image of the visual scene onto the retina. <strong>B.</strong> The retina is composed of different layers of neurons: photoreceptors, horizontal cells, biopolar cells, amacrine cells and ganglion cells. The photoreceptors transform the light signals into electrical signals, and the ganglion cells transmit the visual information to the brain via the optic nerve. <strong>C.</strong> Using a grid of electrodes (yellow dots), it is possible to measure the activity of the ganglion cells (visible in green) from an explanted retina in response to diverse visual stimuli.
</center>



## 1.1. Loading the dataset

The data with the electrode activity you will use is stored in `electrode_recording.mat`. The next code cell loads this file containnig the recorded signal for one electrode.

In [1]:
!gdown 1ky_LanGLT_AvAnkQcGt859l5kOqseVV6 # download the dataset

Downloading...
From: https://drive.google.com/uc?id=1ky_LanGLT_AvAnkQcGt859l5kOqseVV6
To: /content/electrode_recording.mat
100% 3.43M/3.43M [00:00<00:00, 70.6MB/s]


In [2]:
# Importing useful libraries and loading the data
import numpy as np
import matplotlib.pyplot as plt
import scipy.io
from scipy import signal

%matplotlib inline

sampling_frequency  = 20000 # in Hz
electrode_activity = np.squeeze(scipy.io.loadmat('electrode_recording.mat')['data'])

print('The recorded signal has %d time points corresponding to %d seconds' %(len(electrode_activity), len(electrode_activity)/sampling_frequency))

The recorded signal has 1200000 time points corresponding to 60 seconds


## 1.2. Data visualisation


We start by visualising the signal corresponding to the first second of recording, showing both the temporal trace and its corresponding spectrogram.

As you can see, this temporal trace has low frequency fluctuations in addition to the spikes. These low frequency fluctuations correspond to the agglomerated activity of all surrounding cells.
> **Question 1**:  By inspecting the spectrogram, can you suggest a good cut-off frequency for a high-pass filter, such that low frequency fluctuations are removed but spikes are conserved?

#YOUR ANSWER HERE

# 2. Preprocessing with a high-pass filter

As we have just seen, there are some low frequency fluctuations present in the recording in addition to the spikes. We would like to remove these low frequency fluctuations with a high-pass filter.

>**Question 2**: Apply a high-pass filter to the temporal trace to remove the low-frequency fluctations. Plot the temporal trace before and after applying the filter, in two separate plots, for the first second of the signal. Add x and y labels and legends to your plots. Time should be in seconds.

In [4]:
#CODE YOUR SOLUTION HERE

In [5]:
#FIND SOME HELP HERE

from scipy.signal import lfilter
# info here: https://docs.scipy.org/doc/scipy/reference/generated/scipy.signal.lfilter.html

# Filter the data
cutoff = 0  # desired cutoff frequency of the filter, Hz
wc = cutoff/sampling_frequency
electrode_activity_filtered = lfilter(np.array([1-wc, wc-1]), np.array([1, wc-1]), electrode_activity)

# Plot both the original and filtered signals in two different subplots.
fig, axs = plt.subplots(2,1,figsize = (20,8))

# 3. Detecting spike times

We will now use a threshold to detect spike times.

> **Question 3**: Find the timespoints corresponding to a spike using a threshold criterion: when the activity crosses a certain threshold, store the corresponding temporal index in an array. Choose the appropriate threshold based on the vizualisations from the previous section.

**Note:** The resulting array should contain all the spike's time indices.

In [6]:
# CODE YOUR SOLUTION HERE

In [7]:
# FIND SOME HELP HERE

thr = 0 # spike detection threshold in microV
spks, = np.where((time[1:]<thr)*(time[:-1]>thr)) # replace "time" with the correct variable
print('Spikes are in positions:')
print(spks)

Spikes are in positions:
[]


# 4. Spike waveform vizualisation

We are now going to vizualise the waveforms of the detected spikes.

> **Question 3**: Store all the spike waveforms into a matrix: for each spike, select a window of 51 time bins centered on the spike time, and store the corresponding waveform in matrix `waveforms`. Plot all the waveforms on top of each other.

**Note:** Matrix `waveform` should be of size $number\_of\_spikes \times 51$.

In [8]:
# CODE YOUR SOLUTION HERE

> **Question 4**: Can you visually identify different waveforms which could correspond to different cells?

#YOUR ANSWER HERE

# 5. Spike waveform vizualisation in PCA space

We are now going to vizualise the waveforms in a low dimensional space. We will use PCA to identify a low dimensional space preserving most of the variance of the data. We will then represent waveforms projected onto the two principal components of PCA.

> **Question 5**: Use PCA to vizualise the waveforms in a lower dimensional space. To do so:
>  1. Compute the covariance matrix of the waveform matrix. The covariance matrix should have size `51`x`51`. Plot this covariance matrix using `imshow`.
>  2. Apply PCA to this covariance matrix (you can use [np.linalg.eig](https://numpy.org/doc/stable/reference/generated/numpy.linalg.eig.html)).
>  3. Sort the eigenvalues in descending order and plot them (you can use [np.sort](https://numpy.org/doc/stable/reference/generated/numpy.sort.html)).
>  4. Plot the eigenvectors corresponding to the two first eigenvalues.
>  5. Project the waveform data onto these two first eigenvectors, and plot the resulting projections in a 2D scatter plot (each point corresponds to one waveform, x-axis is PC1 and y-axis is PC2).


In [9]:
# CODE YOUR SOLUTION HERE

>  **Question 6**: By inspecting this scatter plot, do you find well-defined clusters? Does this suggest that this electrode is recording from more than one cell?

#YOUR ANSWER HERE

# 6. Isolating the different cells with K-means
In order to isolate the different types of waveforms, we will cluster the waveforms using K-means.

> **Question 7**: Apply K-means clustering to the waveform matrix. Try `K = 2` and `K = 3`.
> 1. For each number of clusters K, repeat the plot from question 3, representing all the waveforms on top of each other, using a different color for each subset of waveforms corresponding to a different cluster.
> 2. For each number of cluster K, repeat the last plot from question 5, the scatterplot of waveforms projected in principal component space, using a different color for each subset of points corresponding to a different cluster.


In [10]:
# CODE YOUR SOLUTION HERE

> **Question 8**: By visually inspecting the results of K-means in PC space and waveform space, can you decide how many different cells this electrode is recording from. What is your level of certainty?

#YOUR ANSWER HERE